# Introduction
This notebook creates a grid for a group of points. Air pollution data is given for equally distributed points. In this notebook, we are going to create polygons centered on those data points. 

Note: Ideally, we would perform this task with Voronoi Polygons. However, when using Voronoi polygons, we will loose the more external datapoints as they will shapes that are not square. The code for doing this is left commented below in case we want to use it in the future.

In [1]:
import pandas as pd
import json
from shapely import Point
import geopandas as gpd
from shapely.geometry import box
import numpy as np

import geopandas as gpd
import numpy as np
from shapely.geometry import Polygon, MultiPolygon
from shapely.ops import unary_union, polygonize
from scipy.spatial import Voronoi

## Calculate polygons centered on the datapoints
Note: This might result in undesireable slivers. For avoiding this, the Voronoi Polygons must be calculated

In [2]:
def extract_point(x):
    data = json.loads(x)
    lat = data['coordinates'][1]
    lon = data['coordinates'][0]
    return Point(lon, lat)

def extract_lat(x):
    data = json.loads(x)
    lat = data['coordinates'][1]
    return lat

def extract_lon(x):
    data = json.loads(x)
    lon = data['coordinates'][0]
    return lon

### Baghdad 

In [3]:
points = pd.read_csv('~/Downloads/20230101.csv')

In [4]:
points['geometry'] = points['.geo'].apply(lambda x: extract_point(x))
points['lat'] = points['.geo'].apply(lambda x: extract_lat(x))
points['lon'] = points['.geo'].apply(lambda x: extract_lon(x))

In [5]:
delta_lon = np.abs(points.loc[6074]['lon'] - points.loc[6075]['lon'])
delta_lat = np.abs(points.loc[6074]['lat'] - points.loc[6043]['lat'])

In [6]:
half_width = delta_lon/2

# Function to create a square polygon from a centroid
def make_square(lon, lat, half_size):
    return box(lon - half_size, lat - half_size, lon + half_size, lat + half_size)

# Apply the function to each row
points["geometry"] = points.apply(lambda row: make_square(row["lon"], row["lat"], half_width), axis=1)
gdf = gpd.GeoDataFrame(points, geometry = points['geometry'], crs = 'epsg:4326')

In [7]:
gdf.explore()

In [8]:
gdf.reset_index(inplace = True)
gdf.index.name = 'geom_id'
gdf = gdf[['geometry']]
gdf.to_file('grid_badhdad.gpkg')

### Addis Ababa

In [11]:
points = pd.read_csv('~/Downloads/.csv')

In [4]:
points['geometry'] = points['.geo'].apply(lambda x: extract_point(x))
points['lat'] = points['.geo'].apply(lambda x: extract_lat(x))
points['lon'] = points['.geo'].apply(lambda x: extract_lon(x))

In [5]:
delta_lon = np.abs(points.loc[6074]['lon'] - points.loc[6075]['lon'])
delta_lat = np.abs(points.loc[6074]['lat'] - points.loc[6043]['lat'])

In [6]:
half_width = delta_lon/2

# Function to create a square polygon from a centroid
def make_square(lon, lat, half_size):
    return box(lon - half_size, lat - half_size, lon + half_size, lat + half_size)

# Apply the function to each row
points["geometry"] = points.apply(lambda row: make_square(row["lon"], row["lat"], half_width), axis=1)
gdf = gpd.GeoDataFrame(points, geometry = points['geometry'], crs = 'epsg:4326')

In [10]:
gdf.explore()

In [8]:
gdf.reset_index(inplace = True)
gdf.index.name = 'geom_id'
gdf = gdf[['geometry']]
gdf.to_file('grid_addis_ababa.gpkg')

In [12]:
# Option with Voronoi
# # 1. Create the data
# projected_crs = 'EPSG:32638'
# gdf_points = gpd.GeoDataFrame(air_baghdad, geometry = air_baghdad['geometry'], crs = 'epsg:4326')
# gdf_points = gdf_points.to_crs(projected_crs)

# # 2. Extract coordinates
# coords = np.array([(point.x, point.y) for point in gdf_points.geometry])

# # 3. Compute the Voronoi diagram
# vor = Voronoi(coords)

# # 4. Create Voronoi polygons
# lines = [
#     [vor.vertices[i] for i in region]
#     for region in vor.regions
#     if len(region) > 0 and -1 not in region
# ]

# polygons = [Polygon(line) for line in lines if Polygon(line).is_valid]

# # 5. Intersect with a bounding box (e.g., convex hull or manual bbox)
# boundary = gdf_points.unary_union.convex_hull.buffer(1000)  # Optional: buffer to expand boundary
# voronoi_clipped = [poly.intersection(boundary) for poly in polygons]

# # 6. Create a GeoDataFrame for Voronoi polygons
# gdf_voronoi = gpd.GeoDataFrame(geometry=voronoi_clipped, crs=gdf_points.crs)

# gdf_voronoi.index.name = 'geom_id'
# gdf_voronoi['area'] = gdf_voronoi['geometry'].apply(lambda x: x.area)
# gdf_voronoi.explore()

/tmp/ipykernel_48540/2480843615.py:22: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  boundary = gdf_points.unary_union.convex_hull.buffer(1000)  # Optional: buffer to expand boundary
